In [1]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib import cm
from mpl_toolkits.mplot3d import Axes3D
%matplotlib inline
%config InlineBackend.figure_format='retina'

# Velocity-pressure formulation of flow past an obstacle

Navier-Stokes momentum equations (2D) and Poisson pressure equation:

$$\frac{\partial u}{\partial t}+u\frac{\partial u}{\partial x}+v\frac{\partial u}{\partial y} = -\frac{1}{\rho}\frac{\partial p}{\partial x}+\nu \left(\frac{\partial^2 u}{\partial x^2}+\frac{\partial^2 u}{\partial y^2} \right)$$

$$\frac{\partial v}{\partial t}+u\frac{\partial v}{\partial x}+v\frac{\partial v}{\partial y} = -\frac{1}{\rho}\frac{\partial p}{\partial y}+\nu\left(\frac{\partial^2 v}{\partial x^2}+\frac{\partial^2 v}{\partial y^2}\right)$$

$$\frac{\partial^2 p}{\partial x^2}+\frac{\partial^2 p}{\partial y^2} = -\rho\left(\frac{\partial u}{\partial x}\frac{\partial u}{\partial x}+2\frac{\partial u}{\partial y}\frac{\partial v}{\partial x}+\frac{\partial v}{\partial y}\frac{\partial v}{\partial y} \right)$$

In [131]:
def pressPoisson(p, dx, dy, dt, rho, nu, u, v, nit, o_bot, o_dpth, o_left, o_wdth):
    import numpy as np
    pn = np.empty_like(p)
    b = np.empty_like(p)
    
    # For readibility, the term in square brackets is below
    b[1:-1,1:-1] = (1/dt * ((u[1:-1,2:]-u[1:-1,:-2])/(2*dx) + (v[2:,1:-1]-v[:-2,1:-1])/(2*dy))
                    - ((u[1:-1,2:]-u[1:-1,:-2])/(2*dx))**2
                    - ((v[2:,1:-1]-v[:-2,1:-1])/(2*dy))**2
                    - 2 * (u[2:,1:-1]-u[:-2,1:-1])/(2*dy) * (v[1:-1,2:]-v[1:-1,:-2])/(2*dx))
    
    for n in range(nit):
        pn = np.copy(p)
        p[1:-1,1:-1] = (((pn[1:-1,2:]+pn[1:-1,:-2])*dy**2 + (pn[2:,1:-1]+p[:-2,1:-1])*dx**2)/(2*(dx**2+dy**2))
                        - rho*dx**2*dy**2/(2*(dx**2+dy**2)) * b[1:-1,1:-1])
        # Boundary conditions
        ## at y = Ly (free surface)
        ## The position of the centered second difference makes the pressure be a forward difference, aka (p[-2] - p[-1])/dy
        p[-1,:] = p[-2,:] - rho*nu/dy*(v[-1,:]-2*v[-2,:]+v[-3,:])
        ## at y = 0 (bottom)
        ## This creates a backward difference for the pressure derivative, (p[1] - p[0])/dy
        p[0,:] = p[1,:] - rho*nu/dy*(v[0,:]-2*v[1,:]+v[2,:])
        ## at x = 0 (left)
        ## This is a backward difference for pressure (p[1] - p[0])/dx
        p[:,0] = p[:,1] - rho*nu/dx*(u[:,0]-2*u[:,1]+u[:,2])
        ## at x = Lx (right)
        ## This is a forward difference, (p[-2] - p[-1])/dx
        p[:,-1] = p[:,-2] - rho*nu/dx*(u[:,-1]-2*u[:,-2]+u[:,-3])
        ## Obstacle bottom
        p[o_bot,o_left:(o_left+o_wdth)] = (p[(o_bot-1),o_left:(o_left+o_wdth)] + rho*nu/dy*(v[o_bot,o_left:(o_left+o_wdth)]-
                                           2*v[(o_bot-1),o_left:(o_left+o_wdth)]+v[(o_bot-2),o_left:(o_left+o_wdth)]))
        ## Obstacle top
        p[(o_bot+o_dpth),o_left:(o_left+o_wdth)] = (p[(o_bot+o_dpth+1),o_left:(o_left+o_wdth)] - rho*nu/dy*(v[(o_bot+o_dpth),o_left:(o_left+o_wdth)]-
                                           2*v[(o_bot+o_dpth+1),o_left:(o_left+o_wdth)]+v[(o_bot+o_dpth+2),o_left:(o_left+o_wdth)]))
        ## Obstacle left
        p[o_bot:(o_bot+o_dpth),o_left] = (p[o_bot:(o_bot+o_dpth),(o_left-1)] + rho*nu/dx*(u[o_bot:(o_bot+o_dpth),o_left]) -
                                        2*u[o_bot:(o_bot+o_dpth),(o_left-1)] + u[o_bot:(o_bot+o_dpth),(o_left-2)])
        ## Obstacle right
        p[o_bot:(o_bot+o_dpth),(o_left+o_wdth)] = (p[o_bot:(o_bot+o_dpth),(o_left+o_wdth+1)] - rho*nu/dx*(u[o_bot:(o_bot+o_dpth),(o_left+o_wdth+2)]) -
                                        2*u[o_bot:(o_bot+o_dpth),(o_left+o_wdth+1)] + u[o_bot:(o_bot+o_dpth),(o_left+o_wdth)])
        ## Inside obstacle
        p[(o_bot):(o_bot+o_dpth),(o_left):(o_left+o_wdth)] = 0
        
#         ## Obstacle bottom
#         p[o_bot,o_left:(o_left+o_wdth)] = p[(o_bot-1),o_left:(o_left+o_wdth)]
#         ## Obstacle top
#         p[(o_bot+o_dpth),o_left:(o_left+o_wdth)] = p[(o_bot+o_dpth+1),o_left:(o_left+o_wdth)]
#         ## Obstacle left
#         p[o_bot:(o_bot+o_dpth),o_left] = (p[o_bot:(o_bot+o_dpth),(o_left-1)])
#         ## Obstacle right
#         p[o_bot:(o_bot+o_dpth),(o_left+o_wdth)] = (p[o_bot:(o_bot+o_dpth),(o_left+o_wdth+1)])
                                           
    return p

Recall the pressure gradient on a boundary of the domain:

$$\frac{\partial p}{\partial y} = \rho\nu\frac{\partial^2 v}{\partial y^2}$$

Previously, a second difference for the velocity, but using a non-centered scheme. What if instead, we used a Taylor expansion?

$$v(y=\Delta{y},t)=v(y=0,t)+\frac{\partial{v}}{\partial{y}}\Delta{y}+\frac{\partial^2{v}}{\partial{y^2}}\frac{\Delta{y}^2}{2}+...$$

In [134]:
def cavity_flow():
    import numpy as np
    nx = 201  # x-points
    ny = 101  # y-points
    nit= 50
    c =  1                       # phase propagation speed
    Lx = 20.0
    Ly = 10.0
    nt = 100
    dx = Lx/(nx-1)
    dy = Ly/(ny-1)
    x = np.linspace(0, Lx, nx)
    y = np.linspace(0, Ly, ny)
    X, Y = np.meshgrid(x, y)
    
    ## Obstacle
    o_bot = 40          # bottom boundary of obstacle
    o_dpth = 20         # obstacle depth
    o_left = 70         # left boundary of obstacle
    o_wdth = 5          # obstacle width

    u_start = 1.
    Re = 200
    rho = 1
    nu = dy*o_dpth*u_start/Re
    dt = 0.0001
    
    u = np.ones((ny, nx))*u_start    # Begin steady state
    v = np.zeros((ny, nx))
    p = np.zeros((ny, nx))
    # Initialize boundary conditions
    u[0,:] = 0         # y = 0
    v[0,:] = 0         # y = 0
    u[-1,:] = 0        # y = Ly
    v[-1,:] = 0        # y = Ly
    u[:,0] = u_start   # Ref: Eq. 2.53 "Essential Computational Fluid Dynamics", Zikanov (2010)
    v[:,0] = 0         # x = 0
    u[:,-1] = u[:,-2]  # See Eq. 2.54 "Essential Computational Fluid Dynamics", Zikanov (2010)
    v[:,-1] = 0        # x = Lx
    u[o_bot:(o_bot+o_dpth),o_left:(o_left+o_wdth)] = 0
    v[o_bot:(o_bot+o_dpth),o_left:(o_left+o_wdth)] = 0
    
    for n in range(nt):
        un = np.copy(u)
        vn = np.copy(v)
        p = pressPoisson(p, dx, dy, dt, rho, nu, u, v, nit, o_bot, o_dpth, o_left, o_wdth)
        
        u[1:-1,1:-1] = (un[1:-1,1:-1] - un[1:-1,1:-1]*dt/dx*(un[1:-1,1:-1]-un[1:-1,:-2])
                       - vn[1:-1,1:-1]*dt/dy*(un[1:-1,1:-1]-un[:-2,1:-1])
                       - dt/(2*rho*dx)*(p[1:-1,2:]-p[1:-1,:-2])
                       + nu*(dt/dx**2*(un[1:-1,2:]-2*un[1:-1,1:-1]+un[1:-1,:-2])
                            + dt/dy**2*(un[2:,1:-1]-2*un[1:-1,1:-1]+un[:-2,1:-1])))
        
        v[1:-1,1:-1] = (vn[1:-1,1:-1] - un[1:-1,1:-1]*dt/dx*(vn[1:-1,1:-1]-vn[1:-1,:-2])
                       - vn[1:-1,1:-1]*dt/dy*(vn[1:-1,1:-1]-vn[:-2,1:-1])
                       - dt/(2*rho*dy)*(p[2:,1:-1]-p[:-2,1:-1])
                       + nu*(dt/dx**2*(vn[1:-1,2:]-2*vn[1:-1,1:-1]+vn[1:-1,:-2])
                            + dt/dy**2*(vn[2:,1:-1]-2*vn[1:-1,1:-1]+vn[:-2,1:-1])))

        # Boundary conditions
        u[0,:] = 0         # y = 0
        v[0,:] = 0         # y = 0
        u[-1,:] = 0        # y = Ly
        v[-1,:] = 0        # y = Ly
        u[:,0] = u_start   # Ref: Eq. 2.53 "Essential Computational Fluid Dynamics", Zikanov (2010)
        v[:,0] = 0         # x = 0
        u[:,-1] = u[:,-2]  # See Eq. 2.54 "Essential Computational Fluid Dynamics", Zikanov (2010)
        v[:,-1] = 0        # x = Lx
        #-------------------------------------------------------------
        # Apply boundary conditions to the obstacle
        #-------------------------------------------------------------  
        # zero velocity everywhere at the obstacle
        u[o_bot:(o_bot+o_dpth),o_left:(o_left+o_wdth)] = 0
        v[o_bot:(o_bot+o_dpth),o_left:(o_left+o_wdth)] = 0
    return u, v, p, X, Y

In [135]:
u, v, p, X, Y = cavity_flow()

In [136]:
qres=3
nx = 201  # x-points
ny = 101  # y-points
Lx = 20.0
Ly = 10.0
x = np.linspace(0, Lx, nx)
y = np.linspace(0, Ly, ny)
fig = plt.figure(figsize=(100,50))
plt.contourf(X, Y, p, alpha=0.5)
plt.tick_params(axis='both', which='major', labelsize=40)
cbar = plt.colorbar()
cbar.ax.tick_params(labelsize=50) 
plt.contour(X, Y, p)
plt.quiver(X[::qres,::qres],Y[::qres,::qres],u[::qres,::qres],v[::qres,::qres]) ##plotting velocity
plt.broken_barh([(x[70+1],x[75-2]-x[70+1])],(y[40+1],y[60-2]-y[40+1]), facecolors='grey', alpha=0.8)
plt.xlabel('X')
plt.ylabel('Y');
#plt.title('time_step = ' + str(nt) + ' nu = ' + str(nu), fontsize=40)

NOTE: I edited the object pressure boundary conditions to keep the scheme consistent with:

$$\frac{\partial p}{\partial y} = \rho\nu\frac{\partial^2 v}{\partial y^2}$$

I made it such that a forward or backward difference is selected based on getting $f(x)$ to coincide with the center of the centered-difference for the second derivative of the velocity. I have not done this for the channel boundaries themselves yet.